This is how I compute the NC Grobner basis using the free algebra.
It is limited because it cannot compute beyond n=4 or 5, but the
advantage is that you stay within Sage and you don't need the clunky GAP connection.

In [ ]:
# this method seems to choke at n=6.
def free_algebra_gens(n):
    """
    a pair consisting of the variables of the free algebra
    """
    FA = FreeAlgebra(QQ,implementation='letterplace', names=\
                flatten([['x'+str(i),'y'+str(i)] for i in range(n)])\
                    , order='lex')
    x = [FA('x'+str(i)) for i in range(n)]
    y = [FA('y'+str(i)) for i in range(n)]
    return (x,y)

def module_ideal(n):
    """
    EXAMPLES:
        sage: module_ideal(1)
        Twosided Ideal (x0*y0 - y0*x0, y0*y0, x0, y0) of Free Associative Unital
            Algebra on 2 generators (x0, y0) over Rational Field
        sage: module_ideal(1).groebner_basis(Infinity)
        Twosided Ideal (y0, x0) of Free Associative Unital Algebra on 2 generators (x0, y0) over Rational Field

        # the infinity indicates that it needs to build the full GB
        # replace Infinity by a level number to partially compute it
    """
    (x,y) = free_algebra_gens(n)
    FA = x[0].parent()
    A = [x[i]*x[j]-x[j]*x[i] for i in range(n) for j in range(n) if i<j] # x's commute
    B = [x[i]*y[j]-y[j]*x[i] for i in range(n) for j in range(n)] # x's and y's commute
    C = [y[i]*y[j]+y[j]*y[i] for i in range(n) for j in range(n) if i<j] # y's anticommute
    D = [y[i]^2 for i in range(n)] # y's square to 0
    E = [sum(x[i]**d for i in range(n)) for d in range(1,n+1)] # regular power sums
    F = [sum(x[i]**d*y[i] for i in range(n)) for d in range(n)] # super-symmetric power sums
    my_ideal = FA*(A+B+C+D+E+F)*FA
    return my_ideal

def bigraded_quotient_basis(n, max_gbdeg=Infinity):
    """
    The bigraded basis as a dictionary mapping degrees to bases.
    EXAMPLES::
        sage: bigraded_quotient_basis(3)
    """
    (x,y) = free_algebra_gens(n)
    II = module_ideal(n)
    FA = x[0].parent()
    YY = {} # the basis starts empty and build it up
    XX = [FA.one()] # the monomials of degree 0 (and in general of a given homog degree)
    while XX:
        for b in XX:
            if bidegree(b) not in YY:
                YY[bidegree(b)]=[]
            YY[bidegree(b)].append(b)
        MNS = [a*b for a in XX for b in FA.gens()]
        XX = [mn for mn in MNS if not any(t.lm_divides(mn)\
                for t in II.groebner_basis(max_gbdeg).gens())]
    return YY

def bidegree(mn):
    """
    the bidegree of the monomial `mn`
    """
    return (str(mn).count('x'),str(mn).count('y'))

def mon_to_list_indices(mn):
    """
    change a monomial in the free algebra into a list of pairs ('x', i) or ('y', i)

    EXAMPLES::
        sage: map(mon_to_list_indices, quotient_basis(3))
        [[],
         [('x', 1)],
         [('y', 1)],
         [('x', 2)],
         [('y', 2)],
         [('x', 2), ('x', 1)],
         [('x', 2), ('y', 1)],
         [('x', 2), ('x', 2)],
         [('y', 2), ('x', 1)],
         [('y', 2), ('y', 1)],
         [('y', 2), ('x', 2)],
         [('x', 2), ('x', 2), ('x', 1)],
         [('y', 2), ('x', 2), ('x', 1)]]
    """
    L = [c for c in str(mn) if c!='*']
    return zip(L[::2],map(ZZ, L[1::2]))

def list_indices_to_mon(L, n=None):
    """
    change a list of pairs of ('x', i) or ('y', i) into a monomial
    """
    if n is None:
        if L:
            n = max(p[1] for p in L)+1
        else:
            n=1
    (x,y) = free_algebra_gens(n)
    FA = x[0].parent()
    if L==[]:
        return FA.one()
    return mul(FA(p[0]+str(p[1])) for p in L)

def SymGrp_action(sig, mn):
    """
    Act by the symmetric group on a monomial
    """
    sig = Permutation(sig)
    L = mon_to_list_indices(mn)
    return list_indices_to_mon([(p[0], sig[p[1]]-1) for p in L], len(sig))

def part_to_perm(la):
    """
    A symmetric group element with cycle structure a fixed partition `la`
    EXAMPLES::
        sage: part_to_perm([3,2,1])
        [2, 3, 1, 5, 4, 6]
    """
    out = []
    return Permutation([tuple(range(sum(la[:i])+1,sum(la[:i])+la[i]+1)) \
                        for i in range(len(la))])

def coeff(expr, trm):
    """
    find the coefficient of ``trm`` in ``expr`` assuming that
    - ``expr`` --  an element of the free algebra
    - ``trm`` -- a monomial in the same free algebra
    The weird thing about this is that you can't compute the
    coefficient withing the Free algebra if you are using the
    'letterplace' implementation (which is what we need to compute
    the ideal) so instead I convert to a regular free algebra and
    then take the coefficient
    """
    oldFA = expr.parent()
    newFA = FreeAlgebra(QQ,oldFA.gens())
    return newFA(expr).coefficient(newFA(trm).support()[0])

zee = lambda la: la.centralizer_size() # size of the centralizer of
def SymGrp_frob_im(basis,n):
    """
    Compute the Frobenius image of a submodule of the full quotient polynomial ring
    """
    s = SymmetricFunctions(QQ['q','z'].fraction_field()).s()
    p = s.symmetric_function_ring().p()
    (q,z) = s.base_ring().gens()
    II = module_ideal(n)
    return sum(sum(coeff(II.reduce(SymGrp_action(part_to_perm(la),b)),b) for b in basis)\
               *p(la)/zee(la) for la in Partitions(n))

def graded_SymGrp_frob_im(n):
    """
    Compute the graded q,z-Frobenius image of the full quotient polynomial ring
    EXAMPLES::
        sage: graded_SymGrp_frob_im(1)
        s[1]
        sage: graded_SymGrp_frob_im(2)
        (q+z)*s[1, 1] + s[2]
        sage: graded_SymGrp_frob_im(3)
        (q^3+q^2*z+q*z+z^2)*s[1, 1, 1] + (q^2+q*z+q+z)*s[2, 1] + s[3]
        sage: graded_SymGrp_frob_im(4)
        (q^6+q^5*z+q^4*z+q^3*z^2+q^3*z+q^2*z^2+q*z^2+z^3)*s[1, 1, 1, 1] +
            (q^5+q^4*z+q^4+2*q^3*z+q^2*z^2+q^3+2*q^2*z+q*z^2+q*z+z^2)*s[2, 1, 1] +
            (q^4+q^3*z+q^2*z+q*z^2+q^2+q*z)*s[2, 2] + (q^3+q^2*z+q^2+q*z+q+z)*s[3, 1] + s[4]
    """
    BQB = bigraded_quotient_basis(n,11)
    s = SymmetricFunctions(QQ['q','z'].fraction_field()).s()
    p = s.symmetric_function_ring().p()
    (q,z) = s.base_ring().gens()
    return s(sum(q**d[0]*z**d[1]*SymGrp_frob_im(basis,n) for (d,basis) in BQB.iteritems()))

In [ ]:
graded_SymGrp_frob_im(1)

In [ ]:
graded_SymGrp_frob_im(2)

In [ ]:
graded_SymGrp_frob_im(3)

In [ ]:
graded_SymGrp_frob_im(4)

In [ ]:
#graded_SymGrp_frob_im(5) #dies

In [ ]:
# Formula with respect to the Delta conjecture
SymmetricFunctions(QQ['q','t','z'].fraction_field()).inject_shorthands(verbose=False)
(q,t,z) = s.base_ring().gens()
Ht = s.symmetric_function_ring().macdonald().Ht()
Bmu = lambda mu: sum(t**c1*q**c2 for (c1,c2) in Partition(mu).cells())
def Deltap(f,g):
    """
    Computes \Delta_f'(g) where \Delta_f'(Ht(lambda)) = f[B_\mu-1] Ht(lambda)
    and Ht is the Macdonald symmetric function basis
    """
    return g.parent()(sum(c*f((Bmu(la)-1)*s[[]]).coefficient([])*Ht(la) for (la,c) in Ht(g)))

In [ ]:
s(Deltap(e[[]],e[1])).map_coefficients(lambda c: c.subs(t=0))

In [ ]:
s(Deltap(e[1]+z,e[2])).map_coefficients(lambda c: c.subs(t=0))

In [ ]:
s(Deltap(e[2]+z*e[1]+z^2,e[3])).map_coefficients(lambda c: c.subs(t=0))

In [ ]:
s(Deltap(e[3]+z*e[2]+z^2*e[1]+z^3,e[4])).map_coefficients(lambda c: c.subs(t=0))

In [ ]:
s(Deltap(e[4]+z*e[3]+z^2*e[2]+z^3*e[1]+z^4,e[5])).map_coefficients(lambda c: c.subs(t=0))

In [ ]:
QQ[['x','y','z']]

In [ ]:
# François' master formula for n=1,2,3,4,5
# this is from his paper:
# 
s = SymmetricFunctions(QQ['q','t','z'].fraction_field()).s()  #make sure there are more variables here f
gns=s.base_ring().gens()
(q,t,z) = (gns[0],gns[1],gns[2])
E1=tensor([s[[]],s[1]])
E2=tensor([s[[]],s[2]]) + tensor([s[1],s[1,1]])
E3=tensor([s[[]],s[3]]) + tensor([s[2]+s[1],s[2,1]]) + tensor([s[3]+s[1,1],s[1,1,1]])
E4=tensor([s[[]],s[4]]) + tensor([s[3]+s[2]+s[1],s[3,1]]) + tensor([s[4]+s[2,1]+s[2],s[2,2]])\
+tensor([s[5]+s[4]+s[3,1]+s[3]+s[2,1]+s[1,1],s[2,1,1]]) + tensor([s[6]+s[4,1]+s[3,1]+s[1,1,1],s[1,1,1,1]])
A = s[10]+s[8,1]+s[7,1]+s[6,2]+s[6,1]+s[5,1,1]+s[4,3]+s[4,2]+s[4,1,1]+s[3,1,1]+s[1,1,1,1]
E5=tensor([s[[]],s[5]])+ tensor([A.skew_by(s[1,1,1]),s[4,1]])\
+tensor([s[6]+s[5]+s[4,1]+s[4]+s[3,1]+s[2,2]+s[3]+s[2,1]+s[2],s[3,2]])\
+tensor([A.skew_by(s[1,1]),s[3,1,1]])\
+tensor([s[8]+s[7]+s[6,1]+s[6]+2*s[5,1]+s[4,2]+s[5]+2*s[4,1]+s[3,2]+s[3,1,1]\
         +s[4]+s[3,1]+s[2,2]+s[2,1,1]+s[2,1],s[2,2,1]])\
+tensor([A.skew_by(s[1]),s[2,1,1,1]])\
+tensor([A,s[1,1,1,1,1]])
A42=s[2]+s[2,1]+s[2,2]+s[3]+s[3,1]+s[3,2]+2*s[4]+2*s[4,1]+s[4,2]+s[5]+s[5,1]+2*s[6]+s[6,1]+s[7]+s[8]
A33=s[2, 2] + s[2, 2, 1] + s[3] + s[3, 1] + s[3, 2] + s[4, 1] + s[4, 1, 1] + s[4, 2] + s[5]\
    + s[5, 1] + s[5, 2] + s[6] + s[6, 1] + s[7] + s[7, 1] + s[9]
A222=s[2, 2] + s[2, 2, 1] + s[3, 1, 1] + s[3, 1, 1, 1] + s[3, 2, 1] + s[3, 3, 1] + s[4, 1] + s[4, 1, 1]\
    + 2*s[4, 2] + s[4, 2, 1] + s[4, 3] + s[4, 4] + s[5, 1] + 2*s[5, 1, 1] + 2*s[5, 2] + s[5, 2, 1] + s[5, 3] \
    + s[6] + 2*s[6, 1] + s[6, 1, 1] + 2*s[6, 2] + s[6, 3] + 2*s[7, 1] + s[7, 1, 1] + s[7, 2] + s[8] + 2*s[8, 1] \
    + s[8, 2] + s[9] + s[9, 1] + s[10] + s[10, 1] + s[12]
A321=s[2, 1] + s[2, 1, 1] + s[2, 2] + s[2, 2, 1] + 2*s[3, 1] + 2*s[3, 1, 1] + 3*s[3, 2] + 2*s[3, 2, 1] + s[3, 3] \
    + s[4] + 3*s[4, 1] + 2*s[4, 1, 1] + 4*s[4, 2] + s[4, 2, 1] + 2*s[4, 3] + 2*s[5] + 5*s[5, 1] + 2*s[5, 1, 1] \
    + 4*s[5, 2] + s[5, 3] + 2*s[6] + 5*s[6, 1] + s[6, 1, 1] + 3*s[6, 2] + 3*s[7] + 4*s[7, 1] + s[7, 2] + 3*s[8] \
    + 3*s[8, 1] + 2*s[9] + s[9, 1] + 2*s[10] + s[11]
A2211=s[2, 1, 1] + s[2, 1, 1, 1] + s[2, 2, 1] + s[3, 1, 1] + s[3, 1, 1, 1] + s[3, 2] + 2*s[3, 2, 1] + s[3, 3] \
    + s[3, 3, 1] + s[4, 1] + 3*s[4, 1, 1] + s[4, 1, 1, 1] + 2*s[4, 2] + 3*s[4, 2, 1] + 2*s[4, 3] + s[4, 3, 1] \
    + s[4, 4] + 2*s[5, 1] + 3*s[5, 1, 1] + 4*s[5, 2] + 2*s[5, 2, 1] + 3*s[5, 3] + s[5, 4] + 3*s[6, 1] \
    + 4*s[6, 1, 1] + 4*s[6, 2] + s[6, 2, 1] + 2*s[6, 3] + s[7] + 4*s[7, 1] + 2*s[7, 1, 1] + 4*s[7, 2] + s[7, 3] \
    + s[8] + 4*s[8, 1] + s[8, 1, 1] + 2*s[8, 2] + 2*s[9] + 4*s[9, 1] + s[9, 2] + s[10] + 2*s[10, 1] + 2*s[11] \
    + s[11, 1] + s[12] + s[13]
AA=s[1, 1, 1, 1, 1] + s[3, 1, 1, 1] + s[4, 1, 1, 1] + s[4, 2, 1] + s[4, 3, 1] + s[4, 4] + s[4, 4, 1] \
    + s[5, 1, 1, 1] + s[5, 2, 1] + s[5, 3, 1] + s[6, 1, 1] + s[6, 1, 1, 1] + s[6, 2, 1] + s[6, 3] + s[6, 3, 1] \
    + s[6, 4] + s[7, 1, 1] + s[7, 2] + s[7, 2, 1] + s[7, 3] + s[7, 4] + 2*s[8, 1, 1] + s[8, 2] + s[8, 2, 1] \
    + s[8, 3] + s[9, 1, 1] + s[9, 2] + s[9, 3] + s[10, 1] + s[10, 1, 1] + s[10, 2] + s[11, 1] + s[11, 2] \
    + s[12, 1] + s[13, 1] + s[15]
E6 = tensor([s[[]],s[6]])+\
    tensor([AA.skew_by(s[1,1,1,1]),s[5,1]])+\
    tensor([AA.skew_by(s[1,1,1]),s[4,1,1]])+\
    tensor([AA.skew_by(s[1,1]),s[3,1,1,1]])+\
    tensor([AA.skew_by(s[1]),s[2,1,1,1,1]])+\
    tensor([AA,s[1,1,1,1,1,1]])+\
    tensor([A2211,s[2,2,1,1]]) +\
    tensor([A321,s[3,2,1]]) +\
    tensor([A222,s[2,2,2]]) +\
    tensor([A33,s[3,3]]) +\
    tensor([A42,s[4,2]])
EE = [E1,E2,E3,E4,E5,E6]
fla = lambda la: StandardTableaux(la).cardinality()
def dimensions(m,mp):
    """
    Find the dimensions of the first 5 quotient rings with m sets of
    commuting variables and mp sets of non-commuting variables
    (make sure m + mp<=number of variables in base ring of symmetric functions)
    using François' master formula

    EXAMPLES::
      sage: dimensions(1,0)
      [1, 2, 6, 24, 120, 720]
      sage: dimensions(0,1)
      [1, 2, 4, 8, 16, 32]
      sage: dimensions(2,0)
      [1, 3, 16, 125, 1296, 16807]
      sage: dimensions(1,1)
      [1, 3, 13, 75, 541, 4683]
      sage: dimensions(0,2)
      [1, 3, 10, 35, 126, 462]
      sage: dimensions(3,0)
      [1, 4, 32, 400, 6912, 153664]
      sage: dimensions(2,1)
      [1, 4, 28, 288, 3936, 67328]
      sage: dimensions(1,2)
      [1, 4, 24, 192, 1920, 23040]
      sage: dimensions(0,3)
      [1, 4, 20, 111, 656, 4048]
    """
    gens = EE[0].parent().base_ring().gens()
    my_dict = dict([(a,1) for a in gens[:m]]+[(a,-1) for a in gens[m:m+mp]])
    return [sum(c*s(la)((sum(gens[:m])-sum(gens[m:m+mp]))*s[[]]).coefficient([]).subs(my_dict)*fla(mu)\
                for ((la,mu),c) in Ed) for Ed in EE]
def qt_dimensions(m_list, mp_list):
    """
    the q,t-graded Frobenius image of the first 5 quotient rings
    INPUT:
    - ``m_list`` - list of q,t variables degrees of commuting variables
    - ``mp_list`` - list of z,u variables degrees of anti-commuting variables
    EXAMPLES::
        sage: map(factor, qt_dimensions([q],[]))
        [1,
         q + 1,
         q^3 + 2*q^2 + 2*q + 1,
         q^6 + 3*q^5 + 5*q^4 + 6*q^3 + 5*q^2 + 3*q + 1,
         q^10 + 4*q^9 + 9*q^8 + 15*q^7 + 20*q^6 + 22*q^5 + 20*q^4 + 15*q^3 + 9*q^2 + 4*q + 1,
         q^15 + 5*q^14 + 14*q^13 + 29*q^12 + 49*q^11 + 71*q^10 + 90*q^9 + 101*q^8 + 101*q^7
             + 90*q^6 + 71*q^5 + 49*q^4 + 29*q^3 + 14*q^2 + 5*q + 1]
        sage: qt_dimensions([],[z])
        [1, z + 1, z^2 + 2*z + 1, z^3 + 3*z^2 + 3*z + 1, z^4 + 4*z^3 + 6*z^2 + 4*z + 1]
        sage: qt_dimensions([q],[z])
        [1,
         q + z + 1,
         q^3 + q^2*z + 2*q^2 + 3*q*z + z^2 + 2*q + 2*z + 1,
         q^6 + q^5*z + 3*q^5 + 4*q^4*z + q^3*z^2 + 5*q^4 + 9*q^3*z + 4*q^2*z^2
             + 6*q^3 + 11*q^2*z + 6*q*z^2 + z^3 + 5*q^2 + 8*q*z + 3*z^2 + 3*q + 3*z + 1,
         q^10 + q^9*z + 4*q^9 + 5*q^8*z + q^7*z^2 + 9*q^8 + 14*q^7*z + 5*q^6*z^2 + 15*q^7
              + 29*q^6*z + 15*q^5*z^2 + q^4*z^3 + 20*q^6 + 44*q^5*z + 29*q^4*z^2 + 5*q^3*z^3
              + 22*q^5 + 51*q^4*z + 39*q^3*z^2 + 10*q^2*z^3 + 20*q^4 + 46*q^3*z + 35*q^2*z^2
              + 10*q*z^3 + z^4 + 15*q^3 + 31*q^2*z + 20*q*z^2 + 4*z^3 + 9*q^2 + 15*q*z + 6*z^2
              + 4*q + 4*z + 1]
        sage: qt_dimensions([q,t],[])[:3]
        [1,
         q + t + 1,
         q^3 + q^2*t + q*t^2 + t^3 + 2*q^2 + 3*q*t + 2*t^2 + 2*q + 2*t + 1]
    """
    gens = EE[0].parent().base_ring().gens()
    my_dict = dict([(a,-a) for a in mp_list])
    return [sum(c*s(la)((sum(m_list)-sum(mp_list))*s[[]]).coefficient([]).subs(my_dict)*fla(mu)\
                for ((la,mu),c) in Ed) for Ed in EE]
def qt_frob_im(m_list, mp_list):
    """
    the q,t-graded Frobenius image of the first 5 quotient rings

    INPUT:

    - ``m_list`` - list of q,t variables degrees of commuting variables
    - ``mp_list`` - list of z,u variables degrees of anti-commuting variables

    EXAMPLES::
        sage: qt_frob_im([q],[])[:3]
        [s[1], q*s[1, 1] + s[2], q^3*s[1, 1, 1] + (q^2+q)*s[2, 1] + s[3]]
        sage: qt_frob_im([],[z])
        [s[1],
         z*s[1, 1] + s[2],
         z^2*s[1, 1, 1] + z*s[2, 1] + s[3],
         z^3*s[1, 1, 1, 1] + z^2*s[2, 1, 1] + z*s[3, 1] + s[4],
         z^4*s[1, 1, 1, 1, 1] + z^3*s[2, 1, 1, 1] + z^2*s[3, 1, 1] + z*s[4, 1] + s[5]]
        sage: qt_frob_im([q,t],[])[:3]
        [s[1], (q+z)*s[1, 1] + s[2],
         (q^3+q^2*z+q*z+z^2)*s[1, 1, 1] + (q^2+q*z+q+z)*s[2, 1] + s[3]]
        sage: qt_frob_im([q,t],[])[:3]
        [s[1],
         (q+t)*s[1, 1] + s[2],
         (q^3+q^2*t+q*t^2+t^3+q*t)*s[1, 1, 1] + (q^2+q*t+t^2+q+t)*s[2, 1] + s[3]]
        sage: [f.scalar(s([1]*f.degree())) for f in qt_frob_im([q,t],[])]
        [1,
         q + t,
         q^3 + q^2*t + q*t^2 + t^3 + q*t,
         q^6 + q^5*t + q^4*t^2 + q^3*t^3 + q^2*t^4 + q*t^5 + t^6 + q^4*t
             + q^3*t^2 + q^2*t^3 + q*t^4 + q^3*t + q^2*t^2 + q*t^3,
         q^10 + q^9*t + q^8*t^2 + q^7*t^3 + q^6*t^4 + q^5*t^5 + q^4*t^6
              + q^3*t^7 + q^2*t^8 + q*t^9 + t^10 + q^8*t + q^7*t^2 + q^6*t^3
              + q^5*t^4 + q^4*t^5 + q^3*t^6 + q^2*t^7 + q*t^8 + q^7*t + 2*q^6*t^2
              + 2*q^5*t^3 + 2*q^4*t^4 + 2*q^3*t^5 + 2*q^2*t^6 + q*t^7 + q^6*t
              + q^5*t^2 + 2*q^4*t^3 + 2*q^3*t^4 + q^2*t^5 + q*t^6 + q^4*t^2
              + q^3*t^3 + q^2*t^4]
    """
    gens = EE[0].parent().base_ring().gens()
    my_dict = dict([(a,-a) for a in mp_list])
    return [sum(c*s(la)((sum(m_list)-sum(mp_list))*s[[]]).coefficient([]).subs(my_dict)*s(mu)\
                for ((la,mu),c) in Ed) for Ed in EE]